### Extract All CSV from subfolder/zip

In [ ]:
import os
import zipfile
import shutil

# Define paths
source_dir = "raw_data"
destination_dir = "data"

# Create the destination directory if it doesn't exist
if not os.path.exists(destination_dir):
    os.makedirs(destination_dir)

# Traverse the raw_data directory
for root, dirs, files in os.walk(source_dir):
    for file in files:
        if file.endswith(".zip"):
            zip_path = os.path.join(root, file)
            try:
                # Extract ZIP files
                with zipfile.ZipFile(zip_path, 'r') as zip_ref:
                    for csv_file in zip_ref.namelist():
                        if csv_file.endswith(".csv"):
                            zip_ref.extract(csv_file, destination_dir)
                            # Move the extracted file to the main data folder
                            extracted_file_path = os.path.join(destination_dir, csv_file)
                            final_path = os.path.join(destination_dir, os.path.basename(csv_file))
                            shutil.move(extracted_file_path, final_path)
            except Exception as e:
                print(f"Error processing {zip_path}: {e}")

print("All CSV files have been extracted and moved to the 'data' folder.")


### Merge CSV's

In [ ]:
import pandas as pd
import glob

path = 'data/*.csv'
all_files = glob.glob(path)

dfs = []
i = 0
for filename in all_files:
    df = pd.read_csv(filename, index_col=None, header=0)
    i = i + 1
    print(i)
    dfs.append(df)

combined_df = pd.concat(dfs, axis=0, ignore_index=True)

combined_df 

combined_df.to_csv('cmbn.csv')

### Cmbn.csv Sorting by date

In [1]:
import pandas as pd
data = pd.read_csv('cmbn.csv',index_col=0)

# data['strike'] = data['Ticker'].apply(lambda x : x[13:-6])
# data['option_type'] = data['Ticker'].apply(lambda x : x[-6:-4])
# data['month'] = data['Ticker'].apply(lambda x : x[10:13])
# data['year'] = data['Ticker'].apply(lambda x : x[8:10])
data['Date'] = pd.to_datetime(data['Date'],dayfirst=True)
sort_df = data.sort_values(by=['Date','Time'])

sort_df.to_csv('sorted.csv')

### Filter Crudeoil-I 

In [ ]:
import pandas as pd


df = pd.read_csv('sorted.csv')

df2 = df[df['Ticker'] == 'CRUDEOIL-I.MCX']

df2.to_csv('CRUDEOIL-I.csv')

### Add round into future file

In [4]:
import pandas as pd
df= pd.read_csv('CRUDEOIL-I.csv')
df['Round'] = df['Open'].apply(lambda x: round(x, -2))
df.to_csv('CRUDEOIL-I.csv')

### Create Symbol

In [1]:
import pandas as pd
import calendar

In [4]:
data = pd.read_csv('CRUDEOIL-I.csv',index_col=None)

data['Date'] = pd.to_datetime(data['Date'],yearfirst=True)
data = data.sort_values(by=['Date','Time'])

data['current_month'] = data['Date'].apply(lambda x : x.month)
data['next_month'] = data['Date'].apply(lambda x : 1 if x.month == 12 else x.month+1)
data['day'] = data['Date'].apply(lambda x : x.day)
data['year'] = data['Date'].apply(lambda x : x.year)

def generate_symbol_pe(day,year,current_month,next_month,round_strike):
    
    if day > 15: #14 to be on safe side
        if current_month == 12: # current year + 1 
            return f'CRUDEOIL{int(year.strftime("%y"))+1}{calendar.month_abbr[next_month].upper()}{round_strike}PE.MCX'
        else:
            return f'CRUDEOIL{year.strftime("%y")}{calendar.month_abbr[next_month].upper()}{round_strike}PE.MCX'

    else:
        return f'CRUDEOIL{year.strftime("%y")}{calendar.month_abbr[current_month].upper()}{round_strike}PE.MCX'


def generate_symbol_ce(day,year,current_month,next_month,round_strike):
    
    if day > 15: #14 to be on safe side
        if current_month == 12:
            return f'CRUDEOIL{int(year.strftime("%y"))+1}{calendar.month_abbr[next_month].upper()}{round_strike}CE.MCX'
        else:
            return f'CRUDEOIL{year.strftime("%y")}{calendar.month_abbr[next_month].upper()}{round_strike}CE.MCX'

    else:
        return f'CRUDEOIL{year.strftime("%y")}{calendar.month_abbr[current_month].upper()}{round_strike}CE.MCX'
    

data['symbol_ce'] = data.apply(lambda x : generate_symbol_ce(x['day'],x['Date'],x['current_month'],x['next_month'],int(x['Round'])),axis=1)
data['symbol_pe'] = data.apply(lambda x : generate_symbol_pe(x['day'],x['Date'],x['current_month'],x['next_month'],int(x['Round'])),axis=1)



In [5]:
data.to_csv('CRUDEOIL-I.csv')

### Final Iterations

In [1]:
import pandas as pd

In [8]:
sorted_df = pd.read_csv('sorted.csv') # all data sorted
index_df = pd.read_csv('CRUDEOIL-I.csv')

In [9]:
# log_data = []

# def log(date, symbol, openn, high, low, close):
#     log_data.append([date, symbol, openn, high, low, close])

def get_param(symbol, date, start_time):
    print(symbol, date, start_time)
    if symbol is None:
        print(date, symbol, "Error: Symbol is None","-","-","-")
        return None

    f2 = sorted_df.query(f'Ticker == "{symbol}" & Date == "{date}" & Time >= "{start_time}" & Time').sort_values(by=['Time'])

    if f2.empty:
        print(date, symbol, "Error: No data for this symbol and date","-","-","-")
        return None
    
    
    print(f2.Open.iloc[0])
    
    return f2.Open.iloc[0]

In [11]:
# f2 = sorted_df.query(f'Ticker == "CRUDEOIL23OCT7500CE.MCX" & Date == "2023-10-03" & Time > "09:00:59" & Time').sort_values(by=['Time']).iloc[0]

In [ ]:
index_df['ce_premium'] = index_df.apply(lambda row : get_param(row['symbol_ce'], row['Date'], row['Time']), axis= 1)
# index_df['pe_premium'] = index_df.apply(lambda row : get_param(row['symbol_pe'], row['Date'], row['Time']), axis= 1)

In [ ]:
index_df['pe_premium'] = index_df.apply(lambda row : get_param(row['symbol_pe'], row['Date'], row['Time']), axis= 1)

In [7]:
index_df.to_csv('output.csv')

### Optimized Code


In [8]:
import pandas as pd

# Load data
sorted_df = pd.read_csv('sorted.csv')
index_df = pd.read_csv('CRUDEOIL-I.csv')

# Suppose log_data is defined; if not, define it or remove from print statements
log_data = None

# Sort and set multi-index for fast lookups
sorted_df = sorted_df.sort_values(by=['Ticker', 'Date', 'Time'])
sorted_df.set_index(['Ticker', 'Date', 'Time'], inplace=True)

def get_param(symbol, date, start_time):
    print(date, start_time)
    if symbol is None:
        print(date, symbol, "Error: Symbol is None", "-", "-", "-", log_data)
        return None
    
    try:
        # Extract all rows for given symbol and date using xs (cross-section)
        subset = sorted_df.xs((symbol, date), level=('Ticker', 'Date'))
        
        # Filter rows where Time > start_time
        # subset is indexed by Time at this point
        result = subset[subset.index >= start_time]
        
        if result.empty:
            print(date, symbol, "Error: No data for this symbol and date", "-", "-", "-", log_data)
            return None
        
        # Return the first 'Open' value after start_time
        # print(symbol, date, start_time)
        return result['Open'].iloc[0]
    
    except KeyError:
        # (symbol, date) combo not found
        print(date, symbol, "Error: No data for this symbol and date", "-", "-", "-", log_data)
        return None

# Apply to get ce_premium and pe_premium
print('ce start')

index_df['ce_premium'] = index_df.apply(lambda row: get_param(row['symbol_ce'], row['Date'], row['Time']), axis=1)
print('ce finish')
index_df['pe_premium'] = index_df.apply(lambda row: get_param(row['symbol_pe'], row['Date'], row['Time']), axis=1)


ce start
2023-10-03 09:00:59
2023-10-03 09:01:59
2023-10-03 09:02:59
2023-10-03 09:03:59
2023-10-03 09:04:59
2023-10-03 09:05:59
2023-10-03 09:06:59
2023-10-03 09:07:59
2023-10-03 09:08:59
2023-10-03 09:09:59
2023-10-03 09:10:59
2023-10-03 09:11:59
2023-10-03 09:12:59
2023-10-03 09:13:59
2023-10-03 09:14:59
2023-10-03 09:15:59
2023-10-03 09:16:59
2023-10-03 09:17:59
2023-10-03 09:18:59
2023-10-03 09:19:59
2023-10-03 09:20:59
2023-10-03 09:21:59
2023-10-03 09:22:59
2023-10-03 09:23:59
2023-10-03 09:24:59
2023-10-03 09:25:59
2023-10-03 09:26:59
2023-10-03 09:27:59
2023-10-03 09:28:59
2023-10-03 09:29:59
2023-10-03 09:30:59
2023-10-03 09:31:59
2023-10-03 09:32:59
2023-10-03 09:33:59
2023-10-03 09:34:59
2023-10-03 09:35:59
2023-10-03 09:36:59
2023-10-03 09:37:59
2023-10-03 09:38:59
2023-10-03 09:39:59
2023-10-03 09:40:59
2023-10-03 09:41:59
2023-10-03 09:42:59
2023-10-03 09:43:59
2023-10-03 09:44:59
2023-10-03 09:45:59
2023-10-03 09:46:59
2023-10-03 09:47:59
2023-10-03 09:48:59
2023-10-03 

In [10]:
index_df.to_csv('final_synthetic_option.csv')